In [2]:
import sympy as sp
import matplotlib.pyplot as plt
import numpy as np
import plotly.graph_objects as go

%matplotlib inline
from numpy import *
d2r = np.deg2rad
r2d = np.degrees

In [3]:
from sympy.physics.vector import init_vprinting
init_vprinting(use_latex='mathjax', pretty_print=False)

In [4]:
from sympy.physics.mechanics import dynamicsymbols

### Parámetros DH

In [5]:
theta, alpha, a, d = dynamicsymbols('theta alpha a d')
theta, alpha, a, d 

(theta, alpha, a, d)

### Parámetros del robot

In [7]:
theta1, theta2, theta3 = dynamicsymbols('theta1 theta2 theta3')
theta1, theta2, theta3

(theta1, theta2, theta3)

In [8]:
rot = sp.Matrix([[sp.cos(theta), -sp.sin(theta)*sp.cos(alpha), sp.sin(theta)*sp.sin(alpha)],
                 [sp.sin(theta), sp.cos(theta)*sp.cos(alpha), -sp.cos(theta)*sp.sin(alpha)],
                 [0, sp.sin(alpha), sp.cos(alpha)]])

trans = sp.Matrix([a*sp.cos(theta),a*sp.sin(theta),d])

last_row = sp.Matrix([[0, 0, 0, 1]])

m = sp.Matrix.vstack(sp.Matrix.hstack(rot, trans), last_row)
m

Matrix([
[cos(theta), -sin(theta)*cos(alpha),  sin(alpha)*sin(theta), a*cos(theta)],
[sin(theta),  cos(alpha)*cos(theta), -sin(alpha)*cos(theta), a*sin(theta)],
[         0,             sin(alpha),             cos(alpha),            d],
[         0,                      0,                      0,            1]])

In [9]:
l1 = 0.2
l2 = 0.5
L1 = 0.7

In [62]:
m01 = m.subs({theta:theta1, d:0.034, a:0, alpha:pi/2})
m12 = m.subs({theta:pi/2+theta2, d:0, a:0.08, alpha:0})
m23 = m.subs({theta:-pi/2+theta3, d:0, a:0.14, alpha:0})
m34 = m.subs({theta:pi/2, d:0, a:0, alpha:pi/2})
#m03 = (m01*m12*m23*m34)
m03 = (m01*m12*m23)
mtcp = sp.simplify(m03)
px = mtcp[0,3]
py = mtcp[1,3]
pz = mtcp[2,3]
fx = sp.lambdify((theta1, theta2, theta3), px, 'numpy')
fy = sp.lambdify((theta1, theta2, theta3), py, 'numpy')
fz = sp.lambdify((theta1, theta2, theta3), pz, 'numpy')

In [63]:
mtcp

Matrix([
[-6.12323399573677e-17*sin(theta2 + theta3)*sin(theta1) + 1.0*cos(theta2 + theta3)*cos(theta1), -1.0*sin(theta2 + theta3)*cos(theta1) - 6.12323399573677e-17*sin(theta1)*cos(theta2 + theta3),      1.0*sin(theta1), -8.57252759403147e-18*sin(theta2 + theta3)*sin(theta1) - 2.99951956532372e-34*sin(theta1)*sin(theta2) - 4.89858719658941e-18*sin(theta1)*cos(theta2) - 0.08*sin(theta2)*cos(theta1) + 0.14*cos(theta2 + theta3)*cos(theta1) + 4.89858719658941e-18*cos(theta1)*cos(theta2)],
[ 6.12323399573677e-17*sin(theta2 + theta3)*cos(theta1) + 1.0*sin(theta1)*cos(theta2 + theta3), -1.0*sin(theta2 + theta3)*sin(theta1) + 6.12323399573677e-17*cos(theta2 + theta3)*cos(theta1),     -1.0*cos(theta1),  8.57252759403147e-18*sin(theta2 + theta3)*cos(theta1) - 0.08*sin(theta1)*sin(theta2) + 0.14*sin(theta1)*cos(theta2 + theta3) + 4.89858719658941e-18*sin(theta1)*cos(theta2) + 2.99951956532372e-34*sin(theta2)*cos(theta1) + 4.89858719658941e-18*cos(theta1)*cos(theta2)],
[                          

### Ploteo del área del trabajo del robot

In [84]:
n_theta = 30

theta1s = np.linspace(d2r(-30), d2r(30), n_theta) # desired range of motion for joint 1
theta2s = np.linspace(d2r(-36), d2r(56), n_theta) # desired range of motion for joint 2
theta3s = np.linspace(d2r(-44), d2r(0), n_theta) # desired range of motion for joint 3

total = len(theta1s)*len(theta2s)*len(theta3s)
print(total)

posx = []
posy = []
posz = []

counter = 0

for t1 in theta1s:
    for t2 in theta2s:
        for t3 in theta3s:
            x = float(fx(t1, t2, t3))
            y = float(fy(t1, t2, t3))
            z = float(fz(t1, t2, t3))
            posx.append(x)
            posy.append(y)
            posz.append(z)
#                 y = fy(l1,l2,theta1,theta2)
x = np.array(posx)
y = np.array(posy)
z = np.array(posz)

'''
fig = go.Figure(data=go.Scatter3d(
    x=x, y=y, z=z,
    marker=dict(
        size=4,
        color=z,
        colorscale='Viridis',
    ),
    line=dict(
        color='darkblue',
        width=2
    )
))

'''
data = go.Scatter3d(
    x=x, 
    y=y, 
    z=z,
    mode='markers', 
    opacity=0.025,  
    marker=dict(
        size=4,
        color=z,
        colorscale='Viridis',
        line=dict(
            color='rgb(0, 0, 0)',
            width=1
        )
    ))

layout = go.Layout(
    scene = go.layout.Scene(
    aspectmode='manual',
    aspectratio=go.layout.scene.Aspectratio(
        x=1, y=1, z=1
    ))
)

fig = go.Figure(data=data, layout=layout)

fig.add_trace(go.Scatter3d(
     x=[0,0.0], 
     y=[0,0.0], 
     z=[0,0.1],
     marker=dict(
         symbol='diamond',
         size=5,
         color='rgb(0,0,0)'
     ),
     line=dict(
        color='blue',
        width=3
    )))

fig.add_trace(go.Scatter3d(
     x=[0,0.0], 
     y=[0,0.1], 
     z=[0,0.0],
     marker=dict(
         symbol='diamond',
         size=5,
         color='rgb(0,0,0)'
     ),
     line=dict(
        color='green',
        width=3
    )))

fig.add_trace(go.Scatter3d(
     x=[0,0.1], 
     y=[0,0.0], 
     z=[0,0.0],
     marker=dict(
         symbol='diamond',
         size=5,
         color='rgb(0,0,0)'
     ),
     line=dict(
        color='red',
        width=3
    )))
'''
fig.add_trace(go.Scatter3d(
     x=[x_target], 
     y=[y_target], 
     z=[z_target],
     mode='markers', 
     marker=dict(
         symbol='x',
         size=5,
         color='rgb(255,255,255)'
     )))
'''
fig.show()

27000


In [80]:
target_param = [d2r(35.0), d2r(36.0), d2r(-10)]
target = f(target_param)
#target = np.array([0.18, 0.016, 0.15])
x_target = target[0]
y_target = target[1]
z_target = target[2]
print(target)
# Obtener punto valuando los parámetros

[0.06455602 0.04520261 0.16009332]


In [81]:
def f(param):
    p0 = param[0]
    p1 = param[1]
    p2 = param[2]
    
    point = []
    point = ([fx(p0, p1, p2),
              fy(p0, p1, p2),
              fz(p0, p1, p2)])
    
    return np.array(point)

# Distancia euclidiana
def distance(p1, p2):
    dist = np.linalg.norm(p1-p2)
    return dist

In [82]:
%%time

n_theta = 36
d_n = 20

params = []

theta1s = np.linspace(d2r(-30), d2r(30), n_theta) # desired range of motion for joint 1
theta2s = np.linspace(d2r(-36), d2r(56), n_theta) # desired range of motion for joint 2
theta3s = np.linspace(d2r(-60), d2r(60), n_theta) # desired range of motion for joint 3

for t1 in theta1s:
    for t2 in theta2s:
        for t3 in theta3s:
            x = float(fx(t1, t2, t3))
            y = float(fy(t1, t2, t3))
            z = float(fz(t1, t2, t3))
            posx.append(x)
            posy.append(y)
            posz.append(z)
total = len(theta1s)*len(theta2s)*len(d3s)
print(total)

for theta1 in theta1s:
        for theta2 in theta2s:
            for d3 in d3s:
                params.append([theta1, theta2, d3])

params = np.array(params)
np.random.shuffle(params)

actual_err = 100
required_err = 0.01

counter = 0

points = []

for param in params:
    points.append(f(param))
    new_err = distance(f(param), target)
    counter += 1
    if new_err<actual_err:
        actual_err = new_err
        best_param = param
    if new_err<required_err:
        break

25920
CPU times: user 2.45 s, sys: 6.58 ms, total: 2.45 s
Wall time: 2.46 s


In [83]:
# Setear mejores puntos para el ploteo
best = f(best_param)
x_best = best[0]
y_best = best[1]
z_best = best[2]

points = np.array(points)

print(counter)
print('error actual:', actual_err)
print('parametros:', r2d(best_param))
print('target:', target)
print('achieved:', f(best_param))

982
error actual: 0.007329478484404244
parametros: [ 30.          37.6        -12.06226937]
target: [0.06455602 0.04520261 0.16009332]
achieved: [0.06712616 0.0387553  0.15773792]
